In [1]:
import pandas as pd
import networkx as nx
import math
import plotly.graph_objects as go

In [2]:
file_all = pd.DataFrame()
for chunk in pd.read_csv("tweet_all_lt.csv", chunksize=4):
    file_all = pd.concat([file_all, chunk[chunk["label"]!=0]])
file_tid = pd.read_csv("lt1.csv")
file_orid = pd.read_csv("h_lt_oid.csv")

In [3]:
def to_str(v):
    return str(int(float(v)))
def to_int(v):
    return int(float(v))

In [4]:
file_all["all_tweet_id"] = file_all["all_tweet_id"].map(to_str)

In [5]:
file_all.columns

Index(['Unnamed: 0', 'date', 'hts', 'is_quote', 'is_retweet', 'lat', 'likes',
       'long', 'mentions', 'original_tweet_id', 'quote_count', 'quoted_text',
       'replies', 'retweets', 'text', 'tweet_id', 'user', 'label', 'full_text',
       'original_tweet_label', 'all_tweet_id'],
      dtype='object')

In [6]:
file_all.shape,file_tid.shape, file_orid.shape

((36479, 21), (16310, 34), (4223, 35))

In [7]:
file_tid.columns

Index(['coordinates', 'created_at', 'hashtags', 'media', 'urls',
       'favorite_count', 'id', 'in_reply_to_screen_name',
       'in_reply_to_status_id', 'in_reply_to_user_id', 'lang', 'place',
       'possibly_sensitive', 'retweet_count', 'reweet_id',
       'retweet_screen_name', 'source', 'text', 'tweet_url', 'user_created_at',
       'user_screen_name', 'user_default_profile_image', 'user_description',
       'user_favourites_count', 'user_followers_count', 'user_friends_count',
       'user_listed_count', 'user_location', 'user_name', 'user_screen_name.1',
       'user_statuses_count', 'user_time_zone', 'user_urls', 'user_verified'],
      dtype='object')

In [8]:
file_orid.columns

Index(['coordinates', 'created_at', 'hashtags', 'media', 'urls',
       'favorite_count', 'id', 'in_reply_to_screen_name',
       'in_reply_to_status_id', 'in_reply_to_user_id', 'lang', 'place',
       'possibly_sensitive', 'retweet_count', 'reweet_id',
       'retweet_screen_name', 'source', 'text', 'tweet_url', 'user_created_at',
       'user_screen_name', 'user_default_profile_image', 'user_description',
       'user_favourites_count', 'user_followers_count', 'user_friends_count',
       'user_listed_count', 'user_location', 'user_name', 'user_screen_name.1',
       'user_statuses_count', 'user_time_zone', 'user_urls', 'user_verified',
       'label'],
      dtype='object')

In [9]:
file_tid.describe()

favorite_count            id  in_reply_to_status_id  \
count    16310.000000  1.631000e+04           7.020000e+02   
mean         0.309565  1.250222e+18           1.250056e+18   
std         13.005548  5.268094e+15           7.265457e+15   
min          0.000000  1.237633e+18           1.142829e+18   
25%          0.000000  1.246805e+18           1.247148e+18   
50%          0.000000  1.250914e+18           1.251535e+18   
75%          0.000000  1.255566e+18           1.255537e+18   
max       1322.000000  1.256628e+18           1.256599e+18   

       in_reply_to_user_id  retweet_count     reweet_id  \
count         7.220000e+02   16310.000000  1.504700e+04   
mean          5.863366e+17    3044.295095  1.249924e+18   
std           5.335912e+17    9640.465821  1.013332e+16   
min           7.592510e+05       0.000000  3.826382e+17   
25%           6.155285e+08      77.000000  1.246597e+18   
50%           7.952653e+17     981.000000  1.250881e+18   
75%           1.114653e+18    4727.000000  1.255542e+18   
max           1.255366e+18  657902.000000  1.256605e+18   

       user_favourites_count  user_followers_count  user_friends_count  \
count           1.631000e+04          1.631000e+04        16310.000000   
mean            4.813831e+04          4.429316e+03         2391.845984   
std             7.954261e+04          8.060138e+04         5679.467035   
min             0.000000e+00          0.000000e+00            0.000000   
25%             4.303000e+03          1.342500e+02          260.000000   
50%             1.805150e+04          5.040000e+02          730.000000   
75%             5.732950e+04          1.968750e+03         2494.750000   
max             1.365013e+06          8.617778e+06       125851.000000   

       user_listed_count  user_statuses_count  user_time_zone  
count       16310.000000         1.631000e+04             0.0  
mean           38.071490         6.308213e+04             NaN  
std           263.672583         3.405351e+05             NaN  
min             0.000000         1.000000e+00             NaN  
25%             0.000000         5.633000e+03             NaN  
50%             2.000000         2.147950e+04             NaN  
75%            14.000000         6.604700e+04             NaN  
max         13984.000000         2.840536e+07             NaN

In [10]:
file_orid.describe()

favorite_count            id  in_reply_to_status_id  \
count     4223.000000  4.223000e+03           3.300000e+02   
mean       130.695477  1.247802e+18           1.247556e+18   
std       1119.657124  5.129910e+15           5.036174e+15   
min          0.000000  1.233098e+18           1.238616e+18   
25%          1.000000  1.242874e+18           1.242847e+18   
50%          5.000000  1.247409e+18           1.247421e+18   
75%         25.000000  1.252598e+18           1.252650e+18   
max      37795.000000  1.256614e+18           1.256476e+18   

       in_reply_to_user_id  retweet_count     reweet_id  \
count         3.700000e+02    4223.000000  3.320000e+02   
mean          4.058407e+17     518.681980  1.243782e+18   
std           5.143528e+17    4774.152435  2.564580e+16   
min           1.337271e+06       0.000000  1.018240e+18   
25%           8.908549e+07       1.000000  1.242641e+18   
50%           1.386956e+09       4.000000  1.247088e+18   
75%           9.675768e+17      18.000000  1.252292e+18   
max           1.242472e+18  109806.000000  1.256226e+18   

       user_favourites_count  user_followers_count  user_friends_count  \
count            4223.000000          4.223000e+03         4223.000000   
mean            38054.285579          3.606551e+05         7017.983661   
std             70756.972397          2.503808e+06        23156.122981   
min                 0.000000          0.000000e+00            0.000000   
25%              1707.000000          7.780000e+02          408.000000   
50%              9001.000000          5.274000e+03         1246.000000   
75%             41500.500000          3.573800e+04         4720.000000   
max            691349.000000          4.796528e+07       509305.000000   

       user_listed_count  user_statuses_count  user_time_zone        label  
count        4223.000000         4.223000e+03             0.0  4222.000000  
mean         2186.126450         9.076993e+04             NaN     0.649929  
std         10700.256122         1.728168e+05             NaN     0.810467  
min             0.000000         1.000000e+00             NaN     0.000000  
25%             3.000000         8.525500e+03             NaN     0.000000  
50%            41.000000         3.138400e+04             NaN     0.000000  
75%           367.000000         1.018370e+05             NaN     1.000000  
max        142151.000000         2.800637e+06             NaN     3.000000

In [11]:
tweet_original_tweet_list = []
id_label_dict = {}
for index, row in file_all.iterrows():
    if row["original_tweet_id"] == row["original_tweet_id"]:
        tweet_original_tweet_list.append([str(row["all_tweet_id"]), to_str(row["original_tweet_id"])])
        id_label_dict[str(row["all_tweet_id"])] = int(row["label"])
        id_label_dict[to_str(row["original_tweet_id"])] = -1

In [12]:
user_retweet_dict = {}
user_label_dict = {}
user_friend_dict= {} # how many users the user follow
user_follower_dict = {} # how many users follow the user
for tweets in tweet_original_tweet_list:
    tweet_id = tweets[0]
    original_tweet_id = tweets[1]
    #print(tweet_id, original_tweet_id)
    if len(file_tid[file_tid["id"]==int(tweet_id)]["user_screen_name"]) != 0 and len(file_orid[file_orid["id"]==int(original_tweet_id)]["user_screen_name"]) != 0:
        tid_user = file_tid[file_tid["id"]==int(tweet_id)]["user_screen_name"].values[0]
        orid_user = file_orid[file_orid["id"]==int(original_tweet_id)]["user_screen_name"].values[0]
        user_label_dict[tid_user] = id_label_dict[tweet_id]
        user_label_dict[orid_user] = id_label_dict[original_tweet_id]
        user_friend_dict[tid_user] = file_tid[file_tid["id"]==int(tweet_id)]["user_friends_count"].values[0]
        user_friend_dict[orid_user] = file_orid[file_orid["id"]==int(original_tweet_id)]["user_friends_count"].values[0]
        user_follower_dict[tid_user] = file_tid[file_tid["id"]==int(tweet_id)]["user_followers_count"].values[0]
        user_follower_dict[orid_user] = file_orid[file_orid["id"]==int(original_tweet_id)]["user_followers_count"].values[0]
        if orid_user in user_retweet_dict:
            if tid_user in user_retweet_dict[orid_user]:
                user_retweet_dict[orid_user][tid_user] += 1
            else:
                user_retweet_dict[orid_user][tid_user] = 1
        else:
            user_retweet_dict[orid_user] = {tid_user:1}

In [13]:
G = nx.Graph()

for orid_user in user_retweet_dict:
    for tid_user in user_retweet_dict[orid_user]:
        retweet_num = user_retweet_dict[orid_user][tid_user]
        G.add_edge(orid_user, tid_user, num=retweet_num)

In [14]:
G.number_of_nodes(), G.number_of_edges()

(8638, 8205)

In [15]:
pos = nx.spring_layout(G)

edge_x = []
edge_y = []
for edge in G.edges():
    x0, y0 = pos[edge[0]]
    x1, y1 = pos[edge[1]]
    edge_x.append(x0)
    edge_x.append(x1)
    edge_x.append(None)
    edge_y.append(y0)
    edge_y.append(y1)
    edge_y.append(None)

edge_trace = go.Scatter(
    x=edge_x, y=edge_y,
    line=dict(width=0.5, color='#888'),
    hoverinfo='text',
    mode='lines',
    marker = dict())

node_x = []
node_y = []
for node in G.nodes():
    x, y = pos[node]
    node_x.append(x)
    node_y.append(y)

node_trace = go.Scatter(
    x=node_x, y=node_y,
    mode='markers',
    hoverinfo='text',
    marker=dict(
        showscale=True,
        # colorscale options
        #'Greys' | 'YlGnBu' | 'Greens' | 'YlOrRd' | 'Bluered' | 'RdBu' |
        #'Reds' | 'Blues' | 'Picnic' | 'Rainbow' | 'Portland' | 'Jet' |
        #'Hot' | 'Blackbody' | 'Earth' | 'Electric' | 'Viridis' |
        colorscale='Jet',
        reversescale=True,
        color=[],
        size=[],
        colorbar=dict(
            thickness=15,
            title='Node label',
            xanchor='left',
            titleside='right'
        ),
        line_width=2))

node_adjacencies = []
node_text = []
node_label = []
node_size = []
for node, adjacencies in enumerate(G.adjacency()):
    node_adjacencies.append(len(adjacencies[1]))
    node_text.append(adjacencies[0]+'\n # of connections: '+str(len(adjacencies[1])))
    node_label.append(user_label_dict[adjacencies[0]])
    node_size.append(2*math.log(user_follower_dict[adjacencies[0]]+1,3))

node_trace.marker.color = node_label
node_trace.marker.size = node_size
#node_trace.marker.color = node_adjacencies
node_trace.text = node_text

In [16]:
fig = go.Figure(data=[edge_trace, node_trace],
             layout=go.Layout(
                title='user retweet graph    licensed treatment    number of users: '+\
                str(G.number_of_nodes())  +'    number of original tweet users: ' +\
                 str(node_label.count(-1)),
                titlefont_size=16,
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20,l=5,r=5,t=40),
                annotations=[ dict(
                    text="users are connected if a user has retweeted a tweet from another user",
                    showarrow=False,
                    xref="paper", yref="paper",
                    x=0.005, y=-0.002 ) ],
                xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                )
fig.show()

In [17]:
adj_dict = {}
for node, adjacencies in enumerate(G.adjacency()):
    adj_dict[adjacencies[0]] = len(adjacencies[1])
sort_orders = sorted(adj_dict.items(), key=lambda x: x[1], reverse=True)

In [18]:
sort_list = sorted(nx.connected_components(G), key = len, reverse=True)
com_order_list = []
for i in range(len(sort_list)):
    sub_G = G.subgraph(list((sort_list)[i]))
    adj_dict = {}
    for node, adjacencies in enumerate(sub_G.adjacency()):
        adj_dict[adjacencies[0]] = len(adjacencies[1])
    sort_orders = sorted(adj_dict.items(), key=lambda x: x[1], reverse=True)
    com_order_list.append(sort_orders)

In [19]:
com_order_list[0]

[('BillNeelyNBC', 1124),
 ('RealJamesWoods', 879),
 ('hannahkuchler', 829),
 ('briantylercohen', 656),
 ('CNN', 384),
 ('JewhadiTM', 246),
 ('eugenegu', 228),
 ('brianstelter', 149),
 ('eviefordham', 146),
 ('adamhousley', 119),
 ('niro60487270', 113),
 ('BreitbartNews', 101),
 ('SFdirewolf', 101),
 ('DrDenaGrayson', 101),
 ('thehill', 94),
 ('TomFitton', 86),
 ('mioana', 83),
 ('superyayadize', 77),
 ('CP24', 76),
 ('business', 72),
 ('thedailybeast', 58),
 ('politico', 54),
 ('MailOnline', 48),
 ('QuickTake', 41),
 ('AndrewFeinberg', 41),
 ('FrasierHarry', 40),
 ('DrOz', 40),
 ('ZekeJMiller', 37),
 ('IWasHrren', 35),
 ('OANN', 34),
 ('TheDailyShow', 30),
 ('Solmemes1', 28),
 ('DailyMail', 27),
 ('Rosie', 25),
 ('jilevin', 24),
 ('SAVE__AMERICA', 18),
 ('TheViewFromLL2', 15),
 ('ClimateRealists', 13),
 ('amjoyshow', 13),
 ('AndrewE_Dunn', 13),
 ('LadyQanuck', 13),
 ('TrumpsPrettyWom', 11),
 ('FinancialTimes', 11),
 ('mog7546', 10),
 ('Prosperous1776', 10),
 ('joepennacchio', 10),
 ('n

In [20]:
output_list = []
for com in com_order_list:
    big_num = 0
    for user in com:
        user_name = user[0]
        output_list.append(user_name)
        num = user[1]
        if num>big_num:
            big_num = num
    output_list.append(big_num)
output_list

['BillNeelyNBC',
 'RealJamesWoods',
 'hannahkuchler',
 'briantylercohen',
 'CNN',
 'JewhadiTM',
 'eugenegu',
 'brianstelter',
 'eviefordham',
 'adamhousley',
 'niro60487270',
 'BreitbartNews',
 'SFdirewolf',
 'DrDenaGrayson',
 'thehill',
 'TomFitton',
 'mioana',
 'superyayadize',
 'CP24',
 'business',
 'thedailybeast',
 'politico',
 'MailOnline',
 'QuickTake',
 'AndrewFeinberg',
 'FrasierHarry',
 'DrOz',
 'ZekeJMiller',
 'IWasHrren',
 'OANN',
 'TheDailyShow',
 'Solmemes1',
 'DailyMail',
 'Rosie',
 'jilevin',
 'SAVE__AMERICA',
 'TheViewFromLL2',
 'ClimateRealists',
 'amjoyshow',
 'AndrewE_Dunn',
 'LadyQanuck',
 'TrumpsPrettyWom',
 'FinancialTimes',
 'mog7546',
 'Prosperous1776',
 'joepennacchio',
 'nypost',
 'HindustanTimes',
 'bimalendu71',
 'nancylevine',
 'redianbot',
 'Mhdude1Mhdude1',
 'khtagh',
 'jtblogs',
 'medashtyn',
 'CoronaUpdateBot',
 'Hope012015',
 'businessinsider',
 'csevaluation',
 '5b20be6386164f8',
 'dthomas293',
 'j_gelling',
 'JohnLaprise',
 'JaggerMickOZ',
 'TJ_Ingr

In [21]:
# plot a graph where color indicates opinion type

In [22]:
dc = nx.degree_centrality(G)
sort_orders = sorted(dc.items(), key=lambda x: x[1], reverse=True)
list_name = []
list_cen = []
for i in sort_orders[0:20]:
    list_name.append(i[0])
    list_cen.append(i[1])

In [23]:
list_name,list_cen

(['BillNeelyNBC',
  'RealJamesWoods',
  'hannahkuchler',
  'briantylercohen',
  'CNN',
  'JewhadiTM',
  'eugenegu',
  'brianstelter',
  'eviefordham',
  'adamhousley',
  'NBCNews',
  'niro60487270',
  'BreitbartNews',
  'SFdirewolf',
  'DrDenaGrayson',
  'thehill',
  'NationBreaking',
  'TomFitton',
  'mioana',
  'juliacarriew'],
 [0.13013777932152368,
  0.10177144841959014,
  0.09598240129674655,
  0.07595229825170777,
  0.04445988190343869,
  0.028482111844390413,
  0.026398054880166725,
  0.017251360426073867,
  0.016904017598703254,
  0.01377793215236772,
  0.013314808382540233,
  0.01308324649762649,
  0.011693875188144031,
  0.011693875188144031,
  0.011693875188144031,
  0.01088340859094593,
  0.010304503878661572,
  0.009957161051290957,
  0.009609818223920343,
  0.009262475396549728])

In [24]:
import plotly.express as px
fig = px.bar(x=list_name, y=list_cen, labels={"x":"user name", "y":"degree centrality"}, title="top 20 users with highest degree centrality")
fig.show()